In [1]:
# ---------- IMPORT LIBRARIES ----------------------

In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import sklearn

from sklearn import tree
from sklearn import preprocessing
from sklearn import metrics
from sklearn import model_selection

from sklearn.model_selection import train_test_split
from sklearn.feature_selection import VarianceThreshold

import graphviz

In [3]:
# ---------- FUNCTIONS ----------------------

In [4]:
def preprocess(dataTarget):
    le = preprocessing.LabelEncoder()
    le.fit(dataTarget)
    class_labels = le.transform(dataTarget)
    
    return class_labels

In [5]:
def preprocessData(data):
    data = data.replace('Unknown', np.nan)
    data.dropna(inplace=True)
    
    return data

In [6]:
def buildDt(dataAttrs, dataTarget):
    #construct decision tree
    clf = tree.DecisionTreeClassifier(criterion="entropy")
    clf = clf.fit(dataAttrs, dataTarget)
    
    return clf

In [7]:
def printPred(df, testX, testY):
    predictions = df.predict(testX)
    print(metrics.classification_report(testY, predictions))

In [22]:
def drawGraph(clf, X, Y):
    dot_data = tree.export_graphviz(clf, out_file = None,
                                feature_names =X.columns,
                                class_names= Y,
                                filled = True,
                                rounded= False,
                                special_characters = True
                               )
    graph = graphviz.Source(dot_data)
    return graph

In [9]:
# ---------- PREPROCESS DATA ----------------------

In [10]:
propertyData = pd.read_csv("property_prices.csv")

In [11]:
propertyData = preprocessData(propertyData)

In [12]:
propertyData['lowBand'], propertyData['highBand'] = propertyData['price_bands'].str.split('-', 1).str
propertyData['lowBand'] = propertyData['lowBand'].str[:-1]
propertyData['highBand'] = propertyData['highBand'].str[:-1]

In [13]:
# ---------- FEATURE SELECTION ----------------------

In [14]:
Y = propertyData['lowBand']
X = propertyData.drop(columns=['id','lowBand', 'highBand','price_bands','realestate_agent','date','address', 'suburb_property_count'])

In [15]:
#class_labels = preprocess(Y)


XE = pd.get_dummies(X)
trainX, testX, trainY, testY = train_test_split(np.array(XE), np.array(Y), test_size=0.2)

le = preprocessing.LabelEncoder()
le.fit(trainY)
class_labels = le.inverse_transform([0,1,2,3,4,5,6])
print(le.transform(trainY))
print(class_labels)


[5 4 1 ... 1 5 1]
['0' '1' '2' '200' '400' '600' '800']


C:\Software\Anaconda\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:


In [16]:
clf = buildDt(trainX, trainY)
printPred(clf, testX, testY)


             precision    recall  f1-score   support

          0       0.00      0.00      0.00         2
          1       0.75      0.78      0.76       639
          2       0.68      0.62      0.65       161
        200       0.64      0.58      0.61        84
        400       0.59      0.61      0.60       261
        600       0.57      0.55      0.56       346
        800       0.43      0.43      0.43       285

avg / total       0.63      0.63      0.63      1778



In [23]:
graph = drawGraph(clf, XE, class_labels)

In [24]:
graph

In [ ]:
# ---------- BUILDING MODELS ----------------------